Copyright **`(c)`** 2022 Giovanni Squillero `<squillero@polito.it>`  
[`https://github.com/squillero/computational-intelligence`](https://github.com/squillero/computational-intelligence)  
Free for personal or classroom use; see [`LICENSE.md`](https://github.com/squillero/computational-intelligence/blob/master/LICENSE.md) for details.  


# Lab 3: ES

## Task

Write agents able to play [*Nim*](https://en.wikipedia.org/wiki/Nim), with an arbitrary number of rows and an upper bound $k$ on the number of objects that can be removed in a turn (a.k.a., *subtraction game*).

The goal of the game is to **avoid** taking the last object.

* Task2.1: An agent using fixed rules based on *nim-sum* (i.e., an *expert system*)
* Task2.2: An agent using evolved rules using ES

## Instructions

* Create the directory `lab2` inside your personal course repository for the course 
* Put a `README.md` and your solution (all the files, code and auxiliary data if needed)

## Notes

* Working in group is not only allowed, but recommended (see: [Ubuntu](https://en.wikipedia.org/wiki/Ubuntu_philosophy) and [Cooperative Learning](https://files.eric.ed.gov/fulltext/EJ1096789.pdf)). Collaborations must be explicitly declared in the `README.md`.
* [Yanking](https://www.emacswiki.org/emacs/KillingAndYanking) from the internet is allowed, but sources must be explicitly declared in the `README.md`.



In [20]:
import logging
from pprint import pprint, pformat
from collections import namedtuple
import random
from copy import deepcopy

## The *Nim* and *Nimply* classes

In [21]:
Nimply = namedtuple("Nimply", "row, num_objects")


In [22]:
class Nim:
    def __init__(self, num_rows: int, k: int = None) -> None:
        self._rows = [i * 2 + 1 for i in range(num_rows)]
        self._k = k

    def __bool__(self):
        return sum(self._rows) > 0

    def __str__(self):
        return "<" + " ".join(str(_) for _ in self._rows) + ">"

    @property
    def rows(self) -> tuple:
        return tuple(self._rows)

    def nimming(self, ply: Nimply) -> None:
        row, num_objects = ply
        print(f"k: {self._k}")
        print(f"nimming value: {num_objects}")
        assert self._rows[row] >= num_objects
        assert self._k is None or num_objects <= self._k
        self._rows[row] -= num_objects


## Sample (and silly) startegies 

In [23]:
def pure_random(state: Nim) -> Nimply:
    """A completely random move"""
    row = random.choice([r for r, c in enumerate(state.rows) if c > 0])
    num_objects = random.randint(1, state.rows[row])
    return Nimply(row, num_objects)


In [24]:
def gabriele(state: Nim) -> Nimply:
    """Pick always the maximum possible number of the lowest row"""
    possible_moves = [(r, o) for r, c in enumerate(state.rows) for o in range(1, c + 1)]
    return Nimply(*max(possible_moves, key=lambda m: (-m[0], m[1])))


In [25]:
def adaptive(state: Nim) -> Nimply:
    """A strategy that can adapt its parameters"""
    genome = {"love_small": 0.5}


In [26]:
import numpy as np


def nim_sum(state: Nim) -> int:
    tmp = np.array([tuple(int(x) for x in f"{c:032b}") for c in state.rows])
    xor = tmp.sum(axis=0) % 2
    return int("".join(str(_) for _ in xor), base=2)


def analize(raw: Nim) -> dict:
    cooked = dict()
    cooked["possible_moves"] = dict()
    for ply in (Nimply(r, o) for r, c in enumerate(raw.rows) for o in range(1, c + 1)):
        tmp = deepcopy(raw)
        tmp.nimming(ply)
        cooked["possible_moves"][ply] = nim_sum(tmp)
    return cooked


def optimal(state: Nim) -> Nimply:
    analysis = analize(state)
    logging.debug(f"analysis:\n{pformat(analysis)}")
    spicy_moves = [ply for ply, ns in analysis["possible_moves"].items() if ns != 0]
    if not spicy_moves:
        spicy_moves = list(analysis["possible_moves"].keys())
    ply = random.choice(spicy_moves)
    return ply


## Oversimplified match

In [27]:
logging.getLogger().setLevel(logging.INFO)

strategy = (optimal, pure_random)

nim = Nim(5)
logging.info(f"init : {nim}")
player = 0
while nim:
    ply = strategy[player](nim)
    logging.info(f"ply: player {player} plays {ply}")
    nim.nimming(ply)
    logging.info(f"status: {nim}")
    player = 1 - player
logging.info(f"status: Player {player} won!")


INFO:root:init : <1 3 5 7 9>
INFO:root:ply: player 0 plays Nimply(row=2, num_objects=3)
INFO:root:status: <1 3 2 7 9>
INFO:root:ply: player 1 plays Nimply(row=4, num_objects=1)
INFO:root:status: <1 3 2 7 8>
INFO:root:ply: player 0 plays Nimply(row=3, num_objects=1)
INFO:root:status: <1 3 2 6 8>
INFO:root:ply: player 1 plays Nimply(row=3, num_objects=6)
INFO:root:status: <1 3 2 0 8>
INFO:root:ply: player 0 plays Nimply(row=4, num_objects=2)
INFO:root:status: <1 3 2 0 6>
INFO:root:ply: player 1 plays Nimply(row=4, num_objects=2)
INFO:root:status: <1 3 2 0 4>
INFO:root:ply: player 0 plays Nimply(row=0, num_objects=1)
INFO:root:status: <0 3 2 0 4>
INFO:root:ply: player 1 plays Nimply(row=4, num_objects=1)
INFO:root:status: <0 3 2 0 3>
INFO:root:ply: player 0 plays Nimply(row=4, num_objects=1)
INFO:root:status: <0 3 2 0 2>
INFO:root:ply: player 1 plays Nimply(row=1, num_objects=3)
INFO:root:status: <0 0 2 0 2>
INFO:root:ply: player 0 plays Nimply(row=4, num_objects=1)
INFO:root:status: <0 0

k: None
nimming value: 1
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 4
k: None
nimming value: 5
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 4
k: None
nimming value: 5
k: None
nimming value: 6
k: None
nimming value: 7
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 4
k: None
nimming value: 5
k: None
nimming value: 6
k: None
nimming value: 7
k: None
nimming value: 8
k: None
nimming value: 9
k: None
nimming value: 3
k: None
nimming value: 1
k: None
nimming value: 1
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 1
k: None
nimming value: 2
k: None
nimming value: 3
k: None
nimming value: 4
k: None
nimming value: 5
k: None
nimming value: 6
k: None
nimming value: 7


In [28]:
def nim_sum(state: Nim) -> int:
    nim_sum = state.rows[0]
    for i in range(1, len(state.rows)):
        nim_sum = nim_sum ^ state.rows[i]
    return nim_sum    

In [29]:
def expert(state: Nim):
    count = 0
    one_count = 0
    for rows_value in state.rows:
        if (rows_value > 1):
            count += 1
        if (rows_value == 1):
            one_count += 1
    
    if (count == 1):
        row = None
        row_size = None
        for i in range(len(state.rows)):
                if (state.rows[i] > 1):
                    row = i
                    row_size = state.rows[i]
        if (one_count % 2 == 0):
            print("1")
            return Nimply(row, row_size - 1)
        else:
            print("2")
            return Nimply(row, row_size)
            
    current_nim_sum = nim_sum(state)
    best_row = -1
    nimming_value = -1

    if current_nim_sum != 0:
        for i in range(len(state.rows)):
            if (state.rows[i] ^ current_nim_sum) < state.rows[i]:
                current_nimming_value = state.rows[i] - (state.rows[i] ^ current_nim_sum)
                if state._k is not None and current_nimming_value > state._k:
                    continue
                if current_nimming_value < 1 or current_nimming_value > state.rows[i]:
                    continue
                best_row = i
                nimming_value = current_nimming_value

        if best_row != -1:
            print("3")
            print(f"nimming value: {nimming_value}")
            print(f"k = {state._k}")
            print(f"left = {state.rows[best_row]}")
            return Nimply(best_row, nimming_value)
    
    chosen_variable = None
    variable_chosen = False
    while(not variable_chosen):
        variable = np.random.randint(0, len(state.rows))
        if (state.rows[variable] > 0):
            variable_chosen = True
            chosen_variable = variable
    print("4")
    #print(f"left: {state.rows[chosen_variable]}")
   #print(np.min([state.rows[chosen_variable], state._k]))
    if (state._k == None):
        random_value = np.random.randint(1, state.rows[chosen_variable] + 1)
    else:
        random_value = random_value = np.random.randint(1, np.min([state.rows[chosen_variable], state._k]) + 1)
    #print(f"random: {random_value}")
    return Nimply(variable, random_value) 

In [30]:
def play(state: Nim, strat_one, strat_two):    
    #logging.getLogger().setLevel(logging.INFO)

    strategy = (strat_one, strat_two)

    nim = state

    #logging.info(f"init : {nim}")
    player = 0
    while nim:
        ply = strategy[player](nim)
        print(f"play: ply: {ply}")
        print(f"player: {strategy[player].__name__}")
        #logging.info(f"ply: player {player} plays {ply}")
        nim.nimming(ply)
        #logging.info(f"status: {nim}")
        player = 1 - player
        
    #logging.info(f"status: Player {player} won!")

    return 1 if strategy[player] == expert else 0

In [31]:
strat_one = expert
strat_two = pure_random
num_of_games = 100
start = 5
k = 40
nims = [play(Nim(start + i), expert, pure_random) for i in range(num_of_games)]

3
nimming value: 9
k = None
left = 9
play: ply: Nimply(row=4, num_objects=9)
player: expert
k: None
nimming value: 9
play: ply: Nimply(row=2, num_objects=4)
player: pure_random
k: None
nimming value: 4
3
nimming value: 4
k = None
left = 7
play: ply: Nimply(row=3, num_objects=4)
player: expert
k: None
nimming value: 4
play: ply: Nimply(row=2, num_objects=1)
player: pure_random
k: None
nimming value: 1
3
nimming value: 1
k = None
left = 3
play: ply: Nimply(row=3, num_objects=1)
player: expert
k: None
nimming value: 1
play: ply: Nimply(row=3, num_objects=1)
player: pure_random
k: None
nimming value: 1
1
play: ply: Nimply(row=1, num_objects=2)
player: expert
k: None
nimming value: 2
play: ply: Nimply(row=3, num_objects=1)
player: pure_random
k: None
nimming value: 1
4
play: ply: Nimply(row=0, num_objects=1)
player: expert
k: None
nimming value: 1
play: ply: Nimply(row=1, num_objects=1)
player: pure_random
k: None
nimming value: 1
3
nimming value: 2
k = None
left = 11
play: ply: Nimply(row=

In [32]:
print(f"Winrate of expert: {np.sum(nims) / len(nims)} after {num_of_games} games, playing against {strat_two.__name__}. Having rows parameter on the interval of [{start}, {start + num_of_games}] and having k = {k}")

Winrate of expert: 1.0 after 100 games, playing against pure_random. Having rows parameter on the interval of [5, 105] and having k = 40


In [50]:
class Individual:
    def __init__(self, num_rows: int) -> None:
        
        self.heap_genome = np.array([np.random.random() for _ in range(num_rows)])
        self.heap_genome = self.heap_genome / np.sum(self.heap_genome)
        self.amount_genome = np.array([np.random.random() for _ in range(num_rows)])
        self.amount_genome = self.amount_genome / np.sum(self.amount_genome)
        self.score = 0
        
    def mutate(self, genome):
        mutating_gene = np.random.randint(0, len(genome))
        genome[mutating_gene] += np.random.uniform(-0.05, 0.05)

    def choose_heap(self, state: Nim):
        squared_genome = [np.sqrt(gene) for gene in self.heap_genome]
        counting_sum = self.heap_genome[0]
        squared_roulette_wheel = np.zeros(len(self.heap_genome) + 1)
        counting_sum = 0
        for i in range(len(self.heap_genome)):
            counting_sum += squared_genome[i]
            squared_roulette_wheel[i+1] = counting_sum
        #print(self.genome)
        #print(squared_roulette_wheel)
        heap_number = None
        i = 0
        while(heap_number == None and i < 100):
            i += 1
            roll_value = np.random.uniform(0, squared_roulette_wheel[-1])
            for i in range(len(squared_roulette_wheel) - 1):
                if (squared_roulette_wheel[i] < roll_value and roll_value <= squared_roulette_wheel[i+1] and state.rows[i] != 0):
                    heap_number = i
                    break
        return heap_number
        
                    
                
            
        
    def increase_score(self, score):
        self.score += 1

In [51]:
class Population:
    def __init__(self, nim_problem_size, population_size, tournament_size, offspring_size, is_comma, k = None):
        self.population_size = population_size
        self.tournament_size = tournament_size
        self.offspring_size = offspring_size
        self.is_comma = is_comma
        self.environment = Nim(nim_problem_size, k=k)
        self.cut_of_size = offspring_size - population_size if self.is_comma else offspring_size
        self.population = [Individual(nim_problem_size) for _ in range(self.population_size)]


    
    def play(self, state: Nim, individual_one: Individual, individual_two: Individual) -> Individual:    
        #logging.getLogger().setLevel(logging.INFO)

        individuals = (individual_one, individual_two)
        strategy = (individual_one.strategy, individual_two.strategy)

        nim = state

        #logging.info(f"init : {nim}")
        player = 0
        while nim:
            ply = strategy[player](nim)
            print(f"play: ply: {ply}")
            print(f"player: {strategy[player].__name__}")
            #logging.info(f"ply: player {player} plays {ply}")
            nim.nimming(ply)
            #logging.info(f"status: {nim}")
            player = 1 - player
            
        #logging.info(f"status: Player {player} won!")

        winner = individuals[player]
        return winner

    def simulate(self):
        for i in range(self.population_size):
            for j in range(i, self.population_size):
                winner = self.play(self.environment, self.population[i], self.population[j])
                winner.increase_score()
    
    def print_result(self):
        for individual in self.population:
            print(individual.score)
    




In [52]:
population = Population(5, 30, 30, 30, False)

In [53]:
individual = Individual(5)

In [54]:
individual = Individual(5)
print(individual.choose_heap(Nim(5)))

4


In [55]:
check = np.zeros(5)

In [56]:
n = 100000
for _ in range(n):
    individual = Individual(5)
    check[individual.choose_heap(Nim(5))] += 1

print(check / n)

[0.19829 0.2008  0.19999 0.20186 0.19906]
